In [19]:
import csv
import codecs
import pprint
import re
import xml.etree.cElementTree as ET
import cerberus
import schema
from my_schema import SCHEMA

OSM_PATH = "CSMap2.xml"
file_in = open("CSMap2.xml")
root = ET.parse("CSMap2.xml").getroot()
schema_file = open("my_schema.py")

''' parse file into seperate elements to use in processing nodes one at a time '''
def find_element():
    element = []
    for item in root.find("node"):
        element = ET.dump(item)
        return element

element = find_element()

In [20]:
NODE_FIELDS = ['id', 'lat', 'lon', 'user', 'uid', 'version', 'changeset', 'timestamp']
NODE_TAGS_FIELDS = ['id', 'key', 'value', 'type']
WAY_FIELDS = ['id', 'user', 'uid', 'version', 'changeset', 'timestamp']
WAY_TAGS_FIELDS = ['id', 'key', 'value', 'type']
WAY_NODES_FIELDS = ['id', 'node_id', 'position']

SCHEMA = SCHEMA

LOWER_COLON = re.compile(r'^([a-z]|_)+:([a-z]|_)+')
PROBLEMCHARS = re.compile(r'[=\+/&<>;\'"\?%#$@\,\. \t\r\n]')

In [11]:
##Run only once to create small sample file for running tests
'''
OSM_FILE = "CSMap2"
SAMPLE_FILE = "CSsample2"

k = 10 # Parameter: take every k-th top level element

def get_element(osm_file, tags=('node', 'way', 'relation')):
    """Yield element if it is the right type of tag

    Reference:
    http://stackoverflow.com/questions/3095434/inserting-newlines-in-xml-file-generated-via-xml-etree-elementtree-in-python
    """
    context = iter(ET.iterparse(osm_file, events=('start', 'end')))
    _, root = next(context)
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            yield elem
            root.clear()


with open(SAMPLE_FILE, 'wb') as output:
    output.write(('<?xml version="1.0" encoding="UTF-8"?>\n').encode())
    output.write(('<osm>\n  ').encode())

    # Write every kth top level element
    for i, element in enumerate(get_element(OSM_FILE)):
        if i % k == 0:
            output.write(ET.tostring(element, encoding='utf-8'))

    output.write(('</osm>').encode())'''

In [21]:
'''helper functions for tag assignments in shape_element function'''

def get_element(osm_file, tags=('node', 'way', 'relation')):
    """Yield element if it is the right type of tag"""

    context = ET.iterparse(osm_file, events=('start', 'end'))
    _, root = next(context)
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            yield elem
            root.clear()

def validate_element(element, validator, schema=SCHEMA):
    """Raise ValidationError if element does not match schema"""
    if validator.validate(element, schema) is not True:
        field, errors = next(validator.errors.iteritems())
        message_string = "\nElement of type '{0}' has the following errors:\n{1}"
        error_string = pprint.pformat(errors)
        
        raise Exception(message_string.format(field, error_string))

class UnicodeDictWriter(csv.DictWriter, object):
    """Extend csv.DictWriter to handle Unicode input"""

    def writerow(self, row):
        super(UnicodeDictWriter, self).writerow({
            k: (v.encode('utf-8') if isinstance(v, bytes) else v) for k, v in row.items()
        })

    def writerows(self, rows):
        for row in rows:
            self.writerow(row)

In [22]:
def create_key(key_string):
    """find "k" values and assign seperate keys and tag types"""
    if ":" in key_string:
        new_string = key_string.find(":")
        tag_type = key_string[:new_string]
        new_key = key_string[new_string+1:]
        return [new_key, tag_type]
        
    else:
        new_key = key_string
        tag_type = "regular"
        return [new_key, tag_type]

In [23]:
'''Find secondary tags and add them to tags list of dictionaries'''
def shape_element(element, node_attr_fields=NODE_FIELDS, way_attr_fields=WAY_FIELDS, default_tag_type='regular'):
    """Clean and shape node or way XML element to Python dictionary"""
    
    """element is a node or way"""
    node_attribs = {}
    way_attribs = {}
    way_nodes = []
    tags = []
    if element.tag == 'node':
        for childName, childValue in element.attrib.items():
            if childName in NODE_FIELDS:
                node_attribs[childName] = childValue
            
        for child in element.iter('tag'):    
            dict = {}
            if PROBLEMCHARS.search(child.attrib['k']):
                continue
            else:
                dict['id'] = element.attrib['id']
                dict['key'] = create_key(child.attrib['k'])[0]
                dict['type'] = create_key(child.attrib['k'])[1]
                dict['value'] = child.attrib['v']
            tags.append(dict)
        
        return {'node': node_attribs, 'node_tags': tags}
        
    elif element.tag == 'way':
        
        for childName, childValue in element.attrib.items():
            if childName in WAY_FIELDS:
                way_attribs[childName] = childValue
                
        '''Process way tags like node tags'''
        for child in element.iter('tag'):
            dict = {}
            if PROBLEMCHARS.search(child.attrib['k']):
                continue
            else:
                dict['id'] = element.attrib['id']
                dict['key'] = create_key(child.attrib['k'])[0]
                dict['type'] = create_key(child.attrib['k'])[1]
                dict['value'] = child.attrib['v']
            tags.append(dict)
        print(tags)
        
        for num, child in enumerate(element.iter('nd')):
            dict = {}
            dict['id'] = element.attrib['id']
            dict['node_id'] = child.attrib['ref']
            dict['position'] = num
            way_nodes.append(dict)
            
        return {'way': way_attribs, 'way_nodes': way_nodes, 'way_tags': tags}

In [24]:
NODES_PATH = "nodes.csv"
NODE_TAGS_PATH = "node_tags.csv"
WAYS_PATH = "ways.csv"
WAY_NODES_PATH = "way_nodes.csv"
WAY_TAGS_PATH = "way_tags.csv"

def process_map(file_in, validate):
    """Iteratively process each XML element and write to csv(s)"""

    with codecs.open(NODES_PATH, 'w') as nodes_file, \
         codecs.open(NODE_TAGS_PATH, 'w') as nodes_tags_file, \
         codecs.open(WAYS_PATH, 'w') as ways_file, \
         codecs.open(WAY_NODES_PATH, 'w') as way_nodes_file, \
         codecs.open(WAY_TAGS_PATH, 'w') as way_tags_file:

        nodes_writer = UnicodeDictWriter(nodes_file, NODE_FIELDS)
        node_tags_writer = UnicodeDictWriter(nodes_tags_file, NODE_TAGS_FIELDS)
        ways_writer = UnicodeDictWriter(ways_file, WAY_FIELDS)
        way_nodes_writer = UnicodeDictWriter(way_nodes_file, WAY_NODES_FIELDS)
        way_tags_writer = UnicodeDictWriter(way_tags_file, WAY_TAGS_FIELDS)

        nodes_writer.writeheader()
        node_tags_writer.writeheader()
        ways_writer.writeheader()
        way_nodes_writer.writeheader()
        way_tags_writer.writeheader()                
            
        validator = cerberus.Validator()
        
        
        for element in get_element(file_in, tags=('node', 'way')):
            el = shape_element(element)
            if el:
                if validate is True:
                    validate_element(el, validator)

                if element.tag == 'node':
                    nodes_writer.writerow(el['node'])
                    node_tags_writer.writerows(el['node_tags'])
                elif element.tag == 'way':
                    ways_writer.writerow(el['way'])
                    way_nodes_writer.writerows(el['way_nodes'])
                    way_tags_writer.writerows(el['way_tags'])
                    
schema_file.close()

In [25]:
if __name__ == '__main__':
    # Note: Validation is ~ 10X slower. For the project consider using a small
    # sample of the map when validating.
    process_map(OSM_PATH, validate=True)

[{'id': '4951983', 'key': 'bicycle', 'type': 'regular', 'value': 'no'}, {'id': '4951983', 'key': 'bridge', 'type': 'regular', 'value': 'yes'}, {'id': '4951983', 'key': 'hgv', 'type': 'regular', 'value': 'designated'}, {'id': '4951983', 'key': 'highway', 'type': 'regular', 'value': 'motorway'}, {'id': '4951983', 'key': 'lanes', 'type': 'regular', 'value': '3'}, {'id': '4951983', 'key': 'layer', 'type': 'regular', 'value': '1'}, {'id': '4951983', 'key': 'maxspeed', 'type': 'regular', 'value': '65 mph'}, {'id': '4951983', 'key': 'oneway', 'type': 'regular', 'value': 'yes'}, {'id': '4951983', 'key': 'ref', 'type': 'regular', 'value': 'I 25'}, {'id': '4951983', 'key': 'surface', 'type': 'regular', 'value': 'paved'}]
[{'id': '4951984', 'key': 'bicycle', 'type': 'regular', 'value': 'no'}, {'id': '4951984', 'key': 'hgv', 'type': 'regular', 'value': 'designated'}, {'id': '4951984', 'key': 'highway', 'type': 'regular', 'value': 'motorway'}, {'id': '4951984', 'key': 'lanes', 'type': 'regular', 'v

[{'id': '7671301', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '7671301', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '7671301', 'key': 'cfcc', 'type': 'tiger', 'value': 'A74'}, {'id': '7671301', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7671301', 'key': 'reviewed', 'type': 'tiger', 'value': 'no'}]
[{'id': '7671342', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '7671342', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '7671342', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7671342', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7671342', 'key': 'reviewed', 'type': 'tiger', 'value': 'no'}]
[{'id': '7671437', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '7671437', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7671437', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7671437', 'key': 'reviewed', 'type': 't

[{'id': '7674229', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '7674229', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7674229', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7674229', 'key': 'reviewed', 'type': 'tiger', 'value': 'no'}]
[{'id': '7674525', 'key': 'highway', 'type': 'regular', 'value': 'unclassified'}, {'id': '7674525', 'key': 'name', 'type': 'regular', 'value': 'Lee Street'}, {'id': '7674525', 'key': 'cfcc', 'type': 'tiger', 'value': 'A74'}, {'id': '7674525', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}]
[{'id': '7674545', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '7674545', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '7674545', 'key': 'service', 'type': 'regular', 'value': 'driveway'}]
[{'id': '7674592', 'key': 'access', 'type': 'regular', 'value': 'no'}, {'id': '7674592', 'key': 'highway', 'type': 'regular', 'value': 'track'}, {'id': '7674592', 'key': 'cfcc', 

[{'id': '7675377', 'key': 'highway', 'type': 'regular', 'value': 'residential'}, {'id': '7675377', 'key': 'maxspeed', 'type': 'regular', 'value': '25 mph'}, {'id': '7675377', 'key': 'name', 'type': 'regular', 'value': 'Cougar Place'}, {'id': '7675377', 'key': 'surface', 'type': 'regular', 'value': 'asphalt'}, {'id': '7675377', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7675377', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7675377', 'key': 'name_base', 'type': 'tiger', 'value': 'Cougar'}, {'id': '7675377', 'key': 'name_type', 'type': 'tiger', 'value': 'Pl'}]
[{'id': '7675410', 'key': 'highway', 'type': 'regular', 'value': 'residential'}, {'id': '7675410', 'key': 'maxspeed', 'type': 'regular', 'value': '25 mph'}, {'id': '7675410', 'key': 'name', 'type': 'regular', 'value': 'Snowbird Place'}, {'id': '7675410', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7675410', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7675410', 

[{'id': '7675851', 'key': 'highway', 'type': 'regular', 'value': 'residential'}, {'id': '7675851', 'key': 'name', 'type': 'regular', 'value': 'Steadman Drive'}, {'id': '7675851', 'key': 'surface', 'type': 'regular', 'value': 'asphalt'}, {'id': '7675851', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7675851', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '7675851', 'key': 'name_base', 'type': 'tiger', 'value': 'Steadman'}, {'id': '7675851', 'key': 'name_type', 'type': 'tiger', 'value': 'Dr'}, {'id': '7675851', 'key': 'reviewed', 'type': 'tiger', 'value': 'no'}]
[{'id': '7675852', 'key': 'highway', 'type': 'regular', 'value': 'secondary'}, {'id': '7675852', 'key': 'name', 'type': 'regular', 'value': 'South Rockrimmon Boulevard'}, {'id': '7675852', 'key': 'surface', 'type': 'regular', 'value': 'asphalt'}, {'id': '7675852', 'key': 'cfcc', 'type': 'tiger', 'value': 'A41'}, {'id': '7675852', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '76

...

[{'id': '803541732', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '803574673', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '803574673', 'key': 'service', 'type': 'regular', 'value': 'driveway'}]
[{'id': '803584434', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '803750416', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '803750417', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '804067601', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '804067601', 'key': 'service', 'type': 'regular', 'value': 'driveway'}]
[{'id': '804067602', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '804067602', 'key': 'service', 'type': 'regular', 'value': 'driveway'}]
[{'id': '805209406', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '805209406', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '805209406', 'key': 'service', 'type': 'regular

[{'id': '813164437', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '813164437', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '813164437', 'key': 'service', 'type': 'regular', 'value': 'driveway'}, {'id': '813164437', 'key': 'source', 'type': 'regular', 'value': 'digitalglobe'}]
[{'id': '813164438', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '813164438', 'key': 'source', 'type': 'regular', 'value': 'digitalglobe'}]
[{'id': '813165340', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '813165341', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '813165342', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '813750267', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '813750267', 'key': 'oneway', 'type': 'regular', 'value': 'yes'}]
[{'id': '813752683', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '813752684', 'key': 'highway', 'type': 'regula

[{'id': '814482258', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '814514576', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '814514577', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '814577338', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '814577338', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '814577338', 'key': 'service', 'type': 'regular', 'value': 'driveway'}]
[{'id': '814851548', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '814851548', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '814851548', 'key': 'oneway', 'type': 'regular', 'value': 'yes'}, {'id': '814851548', 'key': 'cfcc', 'type': 'tiger', 'value': 'A74'}, {'id': '814851548', 'key': 'county', 'type': 'tiger', 'value': 'El Paso, CO'}, {'id': '814851548', 'key': 'reviewed', 'type': 'tiger', 'value': 'no'}]
[{'id': '814851549', 'key': 'access', 'type': 'regular', 'value': 'private'}, {

[{'id': '816055487', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '816055795', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '816055795', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '816148157', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '816148157', 'key': 'highway', 'type': 'regular', 'value': 'service'}, {'id': '816148157', 'key': 'service', 'type': 'regular', 'value': 'driveway'}]
[{'id': '816157926', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '816157926', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '816157927', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '816157927', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '816175249', 'key': 'highway', 'type': 'regular', 'value': 'service'}]
[{'id': '816175250', 'key': 'access', 'type': 'regular', 'value': 'private'}, {'id': '816175250', 'key': 'highway', 'type': 'regular', 'val

[{'id': '817592624', 'key': 'bicycle', 'type': 'regular', 'value': 'designated'}, {'id': '817592624', 'key': 'foot', 'type': 'regular', 'value': 'designated'}, {'id': '817592624', 'key': 'highway', 'type': 'regular', 'value': 'cycleway'}]
[{'id': '817592626', 'key': 'footway', 'type': 'regular', 'value': 'sidewalk'}, {'id': '817592626', 'key': 'highway', 'type': 'regular', 'value': 'footway'}]
[{'id': '817592627', 'key': 'crossing', 'type': 'regular', 'value': 'marked'}, {'id': '817592627', 'key': 'footway', 'type': 'regular', 'value': 'crossing'}, {'id': '817592627', 'key': 'highway', 'type': 'regular', 'value': 'footway'}]
[{'id': '817592628', 'key': 'crossing', 'type': 'regular', 'value': 'marked'}, {'id': '817592628', 'key': 'footway', 'type': 'regular', 'value': 'crossing'}, {'id': '817592628', 'key': 'highway', 'type': 'regular', 'value': 'footway'}]
[{'id': '817592629', 'key': 'crossing', 'type': 'regular', 'value': 'marked'}, {'id': '817592629', 'key': 'footway', 'type': 'regul

##Issues

-csv files saved with a blank line between each record.

##Sources

https://github.com/SpecCRA/quiz_preparing_for_database_sql/blob/master/quiz_preparing_for_database_sql.py
